In [0]:
%run ./conf_notebook

Import the data

In [0]:
df_train = ps.read_csv(train_2_csv_file_path)
df_train = df_train.drop('_c0', axis=1)

path name size modificationTime dbfs:/mnt/pqsashrd/data/ann_pred_1.csv/ ann_pred_1.csv/ 0 0 dbfs:/mnt/pqsashrd/data/ann_pred_1_test.csv/ ann_pred_1_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/ann_pred_3.csv/ ann_pred_3.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_1.csv/ clust_pred_1.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_1_test.csv/ clust_pred_1_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_3.csv/ clust_pred_3.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_3_test.csv/ clust_pred_3_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/test_1.csv test_1.csv 38574669 1714569841000 dbfs:/mnt/pqsashrd/data/test_2.csv test_2.csv 35056701 1714569835000 dbfs:/mnt/pqsashrd/data/test_3.csv test_3.csv 25575183 1714569796000 dbfs:/mnt/pqsashrd/data/train_1.csv train_1.csv 81417863 1714569888000 dbfs:/mnt/pqsashrd/data/train_1_partitioned/ train_1_partitioned/ 0 0 dbfs:/mnt/pqsashrd/data/train_2.csv train_2.csv 73764410 1714569886000 dbfs:/mnt/pqsashrd/data/train_3.csv train_3.csv 54130409 1714569868000 dbfs:/mnt/pqsashrd/data/train_3_partitioned/ train_3_partitioned/ 0 0

In [0]:
label_encoder = LabelEncoder()
df_train = df_train.to_pandas()
df_train["attack_cat_encoded"] = label_encoder.fit_transform(df_train["attack_cat"])
df_train = ps.DataFrame(df_train)

In [0]:
X_train = df_train.set_index("attack_cat")
X_train = X_train.drop("attack_cat_encoded", axis=1)
y_train = df_train["attack_cat_encoded"]

Adjusted Rand Index (ARI): This metric measures the similarity between two clusterings by considering all pairs of samples and counting pairs that are assigned in the same or different clusters in the predicted and true clusterings. The ARI is adjusted for chance, which makes it more robust for comparing different clustering algorithms.

Silhouette Coefficient: This metric measures how similar an object is to its own cluster (cohesion) compared to other clusters (separation). The Silhouette Coefficient is calculated for each sample and can range from -1 to +1, where a high value indicates that the object is well matched to its own cluster and poorly matched to neighboring clusters. If most objects have a high value, the clustering configuration is appropriate.

### hdbscan

In [0]:
estimator = LDA(n_components = 2)
X_lda = estimator.fit_transform(ps.DataFrame(X_train).to_pandas(), y_train.to_pandas())
X_lda_df = ps.DataFrame(data=X_lda, columns=['LDA_component_1', 'LDA_component_2'], index=ps.DataFrame(X_train).index)
X_lda_df = X_lda_df.to_pandas()

In [0]:
custom_color_scale = [
    '#800080',  # Purple (no change)
    '#9370db',  # Medium Purple (no change)
    '#6495ed',  # Cornflower Blue (no change)
    '#000080',  # Navy (no change)
    '#6998b3',  # Darker Light Blue (no change)
    "#e4cbd1",  # Medium Violet Red (a darker, more subdued pink)
]

In [0]:
estimator = LDA(n_components = 4)
X_lda = estimator.fit_transform(X_train.to_pandas(), y_train.to_pandas())
X_lda_df_ = ps.DataFrame(data=X_lda, columns=['LDA_component_1', 'LDA_component_2', 'LDA_component_3', 'LDA_component_4'], index=X_train.index)
X_lda_df_ = X_lda_df_.to_pandas()

In [0]:
min_cluster_sizes = [10000]  
min_samples_values = [25, 50, 100, 150, 200] 

In [0]:
for min_cluster_size in min_cluster_sizes:
    for min_samples in min_samples_values:
        print(min_cluster_size, min_samples)
        hdbscan_model = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size, min_samples=min_samples)

        hdbscan_model.fit(X_lda_df_)

        cluster_labels = hdbscan_model.labels_
        n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0)
        n_noise = list(cluster_labels).count(-1)

        print(n_clusters, n_noise, X_lda_df_.shape[0])

        predicted_labels = cluster_labels
        true_labels = y_train.to_numpy()

        ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

        spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
        evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
        silhouette_score = evaluator.evaluate(spark_df)

        print(f"Number of clusters = {n_clusters+1}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")

10000 25
3 3339 175341
Number of clusters = 4: Silhouette Coefficient = 0.39192723149503933, Adjusted Rand Index (ARI) = 0.20317058563757012
10000 50
5 22081 175341
Number of clusters = 6: Silhouette Coefficient = 0.6440187596718887, Adjusted Rand Index (ARI) = 0.5012569723934385
10000 100
5 22821 175341
Number of clusters = 6: Silhouette Coefficient = 0.6393023959474479, Adjusted Rand Index (ARI) = 0.4929806877428834
10000 150
5 28592 175341
Number of clusters = 6: Silhouette Coefficient = 0.5929342529674245, Adjusted Rand Index (ARI) = 0.46406611894282906
10000 200
5 27661 175341
Number of clusters = 6: Silhouette Coefficient = 0.6031249068405174, Adjusted Rand Index (ARI) = 0.46941081758265885


In [0]:
min_cluster_size=10000
min_samples=50
hdbscan_model = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size, min_samples=min_samples, prediction_data=True).fit(X_lda_df_)

cluster_labels = hdbscan_model.labels_
n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0)
n_noise = list(cluster_labels).count(-1)

print(n_clusters, n_noise, X_lda_df_.shape[0])

predicted_labels = cluster_labels
true_labels = y_train.to_numpy()

ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
silhouette_score = evaluator.evaluate(spark_df)

print(f"Number of clusters = {n_clusters}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")

5 22081 175341
Number of clusters = 5: Silhouette Coefficient = 0.6440187596718887, Adjusted Rand Index (ARI) = 0.5012569723934385


In [0]:
single_prob = hdbscan_model.probabilities_  # Get membership functions
soft_clusters = hdbscan.all_points_membership_vectors(hdbscan_model)  # Get membership functions

In [0]:
soft_clusters_ = ps.DataFrame(soft_clusters, index=X_lda_df.index)
soft_clusters_ = soft_clusters_.to_pandas()

In [0]:
X_lda_df["pred"] = predicted_labels
X_lda_df["prob_pred"] = single_prob

In [0]:
X_lda_df_prova = pd.concat([X_lda_df, soft_clusters_], axis=1)

In [0]:
soft_clusters[0]

array([0.24666479, 0.04177815, 0.05416054, 0.03851578, 0.01961163])

In [0]:
X_lda_df_prova

LDA_component_1  LDA_component_2  ...         3         4
attack_cat                                    ...                    
Normal            -1.399163        -1.203757  ...  0.038516  0.019612
Normal            -0.466579        -0.056796  ...  0.030589  0.007995
Normal            -0.898715        -0.832651  ...  0.158330  0.026174
Normal            -1.416703        -0.900997  ...  0.129433  0.060571
Normal             1.330860         1.171787  ...  0.030323  0.026841
...                     ...              ...  ...       ...       ...
Generic            3.619327         0.144617  ...  0.169060  0.217486
Shellcode         -1.136189        -1.788934  ...  0.215826  0.136569
Generic            0.444686        -0.834180  ...  0.085123  0.086868
Generic            4.150412         0.464584  ...  0.116903  0.249494
Generic            4.752913         0.598568  ...  0.105250  0.398549

[175341 rows x 9 columns]

In [0]:
fig = px.scatter(X_lda_df, x='LDA_component_1', y='LDA_component_2', color=X_lda_df["pred"], color_continuous_scale=custom_color_scale)
fig.update_layout(
    title='LDA Scatter Plot in 2D',
    scene = dict(
        xaxis_title='LDA Component 1',
        yaxis_title='LDA Component 2',
    ),
    legend_title='Attack category',
    width=800,
    height=600
)
fig.show()